# Random City Model
_Felix Haumann_

Prerequisites:
- Excel file with city map where Roads are marked with "X"
- Excel map needs to have one lot marked with "D" which is the depot

Model parameters:
- Every road accessible lot will have a house
- House have between 1 and 15 households
- Households are assigned to the houses at (insert probability here)
- Every household can potentially receive parcels
- Probability for a household is (insert probability here)
- The probability is calculated for each household within a house and the resulting parcels then summed up for that house

Model limitations:
- Houses have no orientation so parcels can be delivered to the 'backside'

---
# SETUP

### Library imports

In [1]:
import math
import random
from typing import Tuple, Dict, Any, List

import xlwings as xw
import pandas as pd
import numpy as np
import time
import ast
import csv


from pathfinding.core.diagonal_movement import DiagonalMovement
from pathfinding.core.grid import Grid
from pathfinding.finder.a_star import AStarFinder
from sklearn.cluster import KMeans
from IPython.display import display
import string
from pprint import pprint
from helper import generate_letter_combinations, save_df_as_csv, read_df_from_csv, elapsed_time, export_map_to_excel_with_formatting
from ortools.constraint_solver import routing_enums_pb2
from ortools.constraint_solver import pywrapcp

### Switches
rerun_simulation: decides whether the simulation will be run again or whether the available csv files will be used

In [2]:
rerun_simulation = False

### Paths

In [3]:
# Excel files
blank_wb_city = r"C:\Users\fhaum\OneDrive\401 MASTER - Masterarbeit\04 Kalkulationen\CITY_BLANK.xlsx"
blank_ws_city = "BLANK"

households_wb_city = r"C:\Users\fhaum\OneDrive\401 MASTER - Masterarbeit\04 Kalkulationen\CITY_HOUSEHOLDS.xlsx"
households_ws_city = "HOUSEHOLDS"
households_col_range = "C:CX"

quantity_wb_city = r"C:\Users\fhaum\OneDrive\401 MASTER - Masterarbeit\04 Kalkulationen\CITY_QTY.xlsx"
quantity_ws_city = "QTY"

excel_pathvis_wb = r"C:\Users\fhaum\OneDrive\401 MASTER - Masterarbeit\04 Kalkulationen\pythonProject\PathVisualisation_TEST.xlsx"
excel_pathvis_ws = "VIS"

# CSV filenames
# TODO: add check if csv files are all available
csv_name_map_base = "map_base"
csv_distance_matrix_base = "distance_matrix_district_"

master_house_csv_path = r"C:\Users\fhaum\OneDrive\401 MASTER - Masterarbeit\04 Kalkulationen\pythonProject\csv_files\master_houses_dict.csv"
depots_xy_csv_path = r"C:\Users\fhaum\OneDrive\401 MASTER - Masterarbeit\04 Kalkulationen\pythonProject\csv_files\depots_xy.csv"



### City parameters

In [4]:
# Defining the map boundaries from the Excel file
first_row = 3
first_col = 3
last_row = 102
last_col = 102
num_of_rows = last_row-first_row+1
num_of_cols = last_col-first_col+1
column_range = "C:CX"
skiprows = 1
map_char_street = "X"
map_char_depot = "D"
name_string_depot = "DEPOT"
delivery_districts = {"A": [(0, 0), (33, 23)],
                      "B": [(34, 0), (71, 26)],
                      "C": [(72, 0), (99, 35)],
                      "D": [(0, 24), (34, 47)],
                      "E": [(35, 27), (71, 52)],
                      "F": [(72, 36), (99, 66)],
                      "G": [(0, 48), (34, 71)],
                      "H": [(35, 53), (71, 75)],
                      "I": [(72, 67), (99, 99)],
                      "J": [(0, 72), (34, 99)],
                      "K": [(35, 76), (71, 99)]
                      }

# Pathfinding variables
# These variables are assigned to the cells for pathfinding
# Tiles with val 1 = walkable
# Tiles with val >1 = walkable but higher cost
# Tiles with val 0 or negative = not walkable
# Note: the last tile (end_coordinates) must have a positive value otherwise it cant be reached
path_val_depot = 200
path_val_house = 500
path_val_house_with_parcels = 100
path_val_empty_lot = 0
path_val_road = 1

### System parameters

#### Conventional delivery

In [5]:
par_sys_conv_vehicle_speed = 6

#### Autonomous delivery

In [6]:
par_sys_aut_vehicle_capacity = 1
par_sys_aut_vehicle_speed = 6

### Weights & distributions

In [7]:
# Parcel quantity choices and weights
parcel_quantity_choices = [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10]
parcel_quantity_weights = [0.8996, 0.0634, 0.0233, 0.0085, 0.0031, 0.0011, 0.0004, 0.0001, 0.0001, 0.0001, 0.0001]

# Household size choices and weights
household_size_choices = [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15]
household_size_weights = [0.4, 0.35, 0.045, 0.04, 0.035, 0.03, 0.025, 0.02, 0.015, 0.01, 0.005, 0.0025, 0.0125, 0.005, 0.005]

# Parcel delivery success rate
parcel_success_choices = [True, False]
parcel_success_weights = {"conventional": [0.95, 0.05], "autonomous": [0.97, 0.03]}

---
# Helper functions

In [8]:
def read_excel_map_as_df(wb_path, ws_name, col_range, skiprows, number_of_rows, number_of_cols):
    col_names = list(range(number_of_cols))
    df = pd.read_excel(wb_path, sheet_name=ws_name, usecols=col_range, skiprows=skiprows, nrows=number_of_rows, names=col_names)
    return df

In [9]:
def get_lot_xy_from_lot_name(ref_dict: dict, lot_name:str):
    return ref_dict[lot_name][key_h_xy]

In [10]:
def write_master_house_dict_to_csv(data, filename):

    # Define the fieldnames for the CSV file
    fieldnames = ["lot",
                  key_h_xy,
                  key_h_lot_use,
                  key_h_households,
                  key_h_parcels,
                  key_h_delivery_district,
                  key_h_path_finding_val,
                  key_h_delivery_runs_required]

    # Write the dictionary to the CSV file
    with open(filename, mode='w', newline='') as file:
        writer = csv.DictWriter(file, fieldnames=fieldnames)
        writer.writeheader()
        for key, value in data.items():
            writer.writerow({"lot": key,
                             key_h_xy: value[key_h_xy],
                             key_h_lot_use: value[key_h_lot_use],
                             key_h_households: value[key_h_households],
                             key_h_parcels: value[key_h_parcels],
                             key_h_delivery_district: value[key_h_delivery_district],
                             key_h_path_finding_val: value[key_h_path_finding_val],
                             key_h_delivery_runs_required: value[key_h_delivery_runs_required]})

def read_csv_to_master_house_dict(filename):
    temp_dict = {}

    # Read the CSV file and populate the dictionary
    with open(filename, mode='r') as file:
        reader = csv.DictReader(file)
        for row in reader:
            lot = row["lot"]
            xy = tuple(map(int, row[key_h_xy].strip("()").split(",")))
            lot_use = row[key_h_lot_use]
            households = int(row[key_h_households])
            parcels = int(row[key_h_parcels])
            delivery_district = row[key_h_delivery_district]
            path_finding_val = int(row[key_h_path_finding_val])
            delivery_runs_required = int(row[key_h_delivery_runs_required])
            temp_dict[lot] = {key_h_xy: xy,
                              key_h_lot_use: lot_use,
                              key_h_households: households,
                              key_h_parcels: parcels,
                              key_h_delivery_district: delivery_district,
                              key_h_path_finding_val: path_finding_val,
                              key_h_delivery_runs_required: delivery_runs_required}
    return temp_dict

In [11]:
def write_or_read_depots(depots_xy: list, path: str, read_or_write: str):
    if read_or_write == "w":
        # Writing to CSV file
        with open(path, mode='w', newline='') as file:
            writer = csv.writer(file)
            writer.writerows(depots_xy)
    elif read_or_write == "r":
        # Reading from CSV file
        with open(path, mode='r') as file:
            reader = csv.reader(file)
            depots_xy_read = [(int(row[0]), int(row[1])) for row in reader]
        return depots_xy_read

---
# Define central datastructures

In [12]:
master_houses_dict = {}

# IMPORTANT: CHANGES TO DICT STRUCTURE REQUIRE INTEGRATION INTO IMPORT AND EXPORT FUNCTION

key_h_xy = "xy"
key_h_lot_use = "lot_use"
key_h_path_finding_val = "path_finding_val"
key_h_households = "households"
key_h_parcels = "parcels"
key_h_delivery_district = "delivery_district"
key_h_delivery_runs_required = "delivery_runs_required"  # Depending on carry capacity autonomous vehicles might have to drive to house more often
# Final format will be: {"AAA":{"xy":(0,0), "lot_use":"P", "households":2, "parcels":4, "deliver_district":"A", "delivery_runs_required":4}, "AAB":{"xy":(1,0), "lot_use": ".", "households":0, "parcels":0, "delivery_district":"", "delivery_runs_required":0}}

In [13]:
def populate_master_houses_dict(height:int = 100, width:int = 100):
    letter_combinations = generate_letter_combinations()

    for y in range(width):
        for x in range(height):
            name = next(letter_combinations)
            master_houses_dict[name] = {key_h_xy: (x, y), key_h_lot_use: None, key_h_households: 0, key_h_parcels: 0, key_h_delivery_district: "", key_h_path_finding_val:0, key_h_delivery_runs_required:0}

populate_master_houses_dict()

In [14]:
pprint(master_houses_dict)

{'AAA': {'delivery_district': '',
         'delivery_runs_required': 0,
         'households': 0,
         'lot_use': None,
         'parcels': 0,
         'path_finding_val': 0,
         'xy': (0, 0)},
 'AAB': {'delivery_district': '',
         'delivery_runs_required': 0,
         'households': 0,
         'lot_use': None,
         'parcels': 0,
         'path_finding_val': 0,
         'xy': (1, 0)},
 'AAC': {'delivery_district': '',
         'delivery_runs_required': 0,
         'households': 0,
         'lot_use': None,
         'parcels': 0,
         'path_finding_val': 0,
         'xy': (2, 0)},
 'AAD': {'delivery_district': '',
         'delivery_runs_required': 0,
         'households': 0,
         'lot_use': None,
         'parcels': 0,
         'path_finding_val': 0,
         'xy': (3, 0)},
 'AAE': {'delivery_district': '',
         'delivery_runs_required': 0,
         'households': 0,
         'lot_use': None,
         'parcels': 0,
         'path_finding_val': 0,
         

In [15]:
# Dict that will contain all the information about the conventional delivery districts

# Final format will be:
# {<districtA>: {"paths":{<vehicle_id1>: ['DEPOT1', 'ATI', 'AXC', 'BMM']}, "path_lengths" : {<vehicle_id1>: 450}},
# <districtB>: {"paths":{<vehicle_id1>: ['DEPOT1', 'ATI', 'AXC', 'BMM']}, "path_lengths" : {<vehicle_id1>: 450}}}
master_routes_dict = {}

key_r_paths = "paths"
key_r_path_lengths = "path_lengths"


In [16]:
# Dict that will contain all the information about the autonomous delivery systems

# Final format will be:
# {<districtA>: {"distance": 1550, "further_parameter": "something"}},
# <districtB>:{"distance": 2540, "further_parameter": "something_else"}}

master_autonomous_dict = {}
key_a_distance = "distance"

---
# Prepare maps

### Base map from Excel

In [17]:
if rerun_simulation:
    map_base = read_excel_map_as_df(wb_path=blank_wb_city, ws_name=blank_ws_city, col_range=column_range,
                                    skiprows=skiprows, number_of_rows=num_of_rows, number_of_cols=num_of_cols)
    save_df_as_csv(map_base, csv_name_map_base)
else:
    map_base = read_df_from_csv(csv_name_map_base)

display(map_base)



0    1    2    3    4    5    6    7    8    9   ...   90   91   92   93   
0   NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...  NaN  NaN  NaN  NaN  \
1   NaN    D  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...  NaN  NaN  NaN  NaN   
2   NaN    X  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...  NaN  NaN  NaN  NaN   
3   NaN    X    X    X    X    X    X    X    X    X  ...    X    X    X    X   
4   NaN    X  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...  NaN    X  NaN  NaN   
..  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...   
95  NaN  NaN    X  NaN  NaN  NaN    X  NaN  NaN  NaN  ...    X  NaN  NaN  NaN   
96  NaN  NaN    X  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...    X  NaN  NaN  NaN   
97    X    X    X    X    X    X    X    X    X    X  ...    X  NaN  NaN  NaN   
98  NaN  NaN    X  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...  NaN  NaN  NaN  NaN   
99  NaN  NaN    X  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...    X    X    X    X   

     94   95   96   97   98   99  
0   NaN  NaN  NaN  NaN  NaN  NaN  
1   NaN  NaN  NaN  NaN  NaN  NaN  
2   NaN  NaN  NaN  NaN  NaN  NaN  
3     X    X    X    X    X    X  
4   NaN  NaN  NaN    X  NaN    X  
..  ...  ...  ...  ...  ...  ...  
95  NaN    X  NaN  NaN    X  NaN  
96  NaN    X  NaN  NaN    X  NaN  
97  NaN    X  NaN  NaN    X  NaN  
98  NaN    X  NaN  NaN    X  NaN  
99    X    X    X    X    X  NaN  

[100 rows x 100 columns]

### Copy base map

In [18]:
map_lot_use = map_base.copy()
map_lot_use = map_lot_use.fillna(0)  # Replace NaN with empty lots

In [19]:
map_parcel = map_base.copy()

In [20]:
map_pathfinding = map_base.copy()

In [21]:
map_lot_names = map_base.copy()

### Map styling

In [22]:
def display_styled_map(map_to_style):
    center_style = [
        {'selector': 'td',
         'props': [('text-align', 'center')]}
    ]
    styled_map = map_to_style.style
    styled_map.set_table_styles(center_style)
    display(styled_map)

---
# Populate city with houses

In [23]:
def lot_next_to_road(map_df: pd.DataFrame, x:int, y:int, map_char_street) -> bool:
    """
    Checks if current lot is next to a road
    """
    own = map_df.iat[y, x]
    above = map_df.iat[y - 1, x] if y - 1 >= 0 else 0
    left = map_df.iat[y, x - 1] if x - 1 >= 0 else 0
    below = map_df.iat[y + 1, x] if y + 1 < map_df.shape[0] else 0
    right = map_df.iat[y, x + 1] if x + 1 < map_df.shape[1] else 0

    #print("own",own, "above",above, "left", left, "right", right, "below",below)  # Debug


    around = {"a": True if above == map_char_street else False,
              "l": True if left == map_char_street else False,
              "r": True if right == map_char_street else False,
              "b": True if below == map_char_street else False}
    any_surround = any(around.values())

    if own != map_char_street and any_surround:
        return True
    else:
        return False


In [24]:
def select_household_size():
    result = random.choices(household_size_choices, household_size_weights, k=1)
    res_int = result[0]
    return res_int

In [25]:
def select_parcel_quantity():
    result = random.choices(parcel_quantity_choices, parcel_quantity_weights, k=1)
    res_int = result[0]
    return res_int

In [26]:
def evaluate_lot_use(map_df: pd.DataFrame) -> list:
    """
    Evaluates every lot in the master_dict for it use.
    If a lot is by a road a house will be places, the households in the house chosen at random based on the choices and weights defined.
    The parcels each household receives which are again based in choices and weights are summed up for each house.
    The master_dict will be edited to incorporate the lot use for printing a pretty map.
    The coordinates of the depot or depots will be returned as list of tuples.
    :param map_df:
    :return: depot_coordinates
    """
    depot_coordinates = []
    for lot, info in master_houses_dict.items():
        x, y = info[key_h_xy]
        cell_val = map_df.iat[y, x]
        if cell_val == 0:
            if lot_next_to_road(map_df, x, y, map_char_street):
                households_in_house = select_household_size()
                parcels_to_house = 0
                for household in range(households_in_house):
                    parcels_to_house += select_parcel_quantity()
                info[key_h_households] = households_in_house
                info[key_h_parcels] = parcels_to_house
                if parcels_to_house > 0:
                    info[key_h_lot_use] = "P"
                    info[key_h_path_finding_val] = path_val_house_with_parcels
                else:
                    info[key_h_lot_use] = "H"
                    info[key_h_path_finding_val] = path_val_house
            else:
                info[key_h_lot_use] = "."
        elif cell_val == map_char_depot:
            info[key_h_lot_use] = map_char_depot
            info[key_h_path_finding_val] = path_val_depot
            depot_coordinates.append(info[key_h_xy])
        elif cell_val == map_char_street:
            info[key_h_lot_use] = " "
            info[key_h_path_finding_val] = path_val_road
        else:
            info[key_h_lot_use] = "WTF"
    return depot_coordinates


In [33]:
if rerun_simulation:
    depots_xy = evaluate_lot_use(map_lot_use)
    write_or_read_depots(depots_xy, depots_xy_csv_path, "w")
    write_master_house_dict_to_csv(master_houses_dict, master_house_csv_path)
    pprint(master_houses_dict)
    print(f"Depot locations: {depots_xy}")
    print("------")
    print("Lot use evaluated")
else:
    print("Reading lot use from csv...")
    depots_xy = write_or_read_depots([], depots_xy_csv_path, "r")
    master_houses_dict = read_csv_to_master_house_dict(master_house_csv_path)
    pprint(master_houses_dict)
    print(f"Depot locations: {depots_xy}")
    print("------")
    print("Lot use read from csv")


{'AAA': {'delivery_district': '',
         'delivery_runs_required': 0,
         'households': 0,
         'lot_use': '.',
         'parcels': 0,
         'path_finding_val': 0,
         'xy': (0, 0)},
 'AAB': {'delivery_district': '',
         'delivery_runs_required': 0,
         'households': 0,
         'lot_use': '.',
         'parcels': 0,
         'path_finding_val': 0,
         'xy': (1, 0)},
 'AAC': {'delivery_district': '',
         'delivery_runs_required': 0,
         'households': 0,
         'lot_use': '.',
         'parcels': 0,
         'path_finding_val': 0,
         'xy': (2, 0)},
 'AAD': {'delivery_district': '',
         'delivery_runs_required': 0,
         'households': 0,
         'lot_use': '.',
         'parcels': 0,
         'path_finding_val': 0,
         'xy': (3, 0)},
 'AAE': {'delivery_district': '',
         'delivery_runs_required': 0,
         'households': 0,
         'lot_use': '.',
         'parcels': 0,
         'path_finding_val': 0,
         'xy':

In [31]:
pprint(master_houses_dict)

{'AAA': {'delivery_district': '',
         'delivery_runs_required': 0,
         'households': 0,
         'lot_use': None,
         'parcels': 0,
         'path_finding_val': 0,
         'xy': (0, 0)},
 'AAB': {'delivery_district': '',
         'delivery_runs_required': 0,
         'households': 0,
         'lot_use': None,
         'parcels': 0,
         'path_finding_val': 0,
         'xy': (1, 0)},
 'AAC': {'delivery_district': '',
         'delivery_runs_required': 0,
         'households': 0,
         'lot_use': None,
         'parcels': 0,
         'path_finding_val': 0,
         'xy': (2, 0)},
 'AAD': {'delivery_district': '',
         'delivery_runs_required': 0,
         'households': 0,
         'lot_use': None,
         'parcels': 0,
         'path_finding_val': 0,
         'xy': (3, 0)},
 'AAE': {'delivery_district': '',
         'delivery_runs_required': 0,
         'households': 0,
         'lot_use': None,
         'parcels': 0,
         'path_finding_val': 0,
         

---
# Populate maps

## Show parcel locations on map

In [ ]:
def populate_parcel_map():
    for name, info in master_houses_dict.items():
        x,y = info[key_h_xy]
        lot_use = info[key_h_lot_use]
        map_parcel.iat[y, x] = lot_use

In [ ]:
populate_parcel_map()
display_styled_map(map_parcel)

## Populate lot names map

In [ ]:
def populate_lot_names_map():
    for name, info in master_houses_dict.items():
        x,y = info[key_h_xy]
        lot_use = info[key_h_lot_use]
        print_name = name if lot_use not in [".", " "] else ""
        lot_use = lot_use if lot_use in ["."] else ""
        map_lot_names.iat[y, x] = f"{print_name}{lot_use}"

In [ ]:
populate_lot_names_map()
display_styled_map(map_lot_names)

---
# Pathfinding

## Setup Pathfinding

#### Transform map for pathfinding

In [ ]:
map_pathfinding = map_pathfinding.replace(map_char_street, -999)  # Replace 'X' values with -999 --> Road
map_pathfinding = map_pathfinding.replace(map_char_depot, -1000)  # Replace 'D' values with -1000 --> Depot
map_pathfinding = map_pathfinding.fillna(path_val_empty_lot) # Replace NaN values with -2 --> Empty lots
map_pathfinding = map_pathfinding.apply(pd.to_numeric, errors='coerce', downcast='integer')  # Transform float values to ints
map_pathfinding = map_pathfinding.mask(map_pathfinding >= 0, -1)  # Replace positive numeric values with -1
map_pathfinding = map_pathfinding.replace(-999, path_val_road)  # Replace -999 values with road_val
map_pathfinding = map_pathfinding.replace(-1000, path_val_depot)  # Replace -1000 values with depot_val

map_pathfinding

### Populate pathfinding map with values from master_dict

In [ ]:
def populate_pathfinding_map():
    for lot, info in master_houses_dict.items():
        x, y = info[key_h_xy]
        path_value = info[key_h_path_finding_val]
        map_pathfinding.iat[y, x] = path_value

In [ ]:
populate_pathfinding_map()
display(map_pathfinding)

In [ ]:
def instantiate_grid(map_df: pd.DataFrame, export_matrix:bool = False):
    pathfinding_map_matrix = map_df.values.tolist()
    grid_export = Grid(matrix=pathfinding_map_matrix)
    if export_matrix:
        return grid_export, pathfinding_map_matrix
    else:
        return grid_export

In [ ]:
def find_path(grid: Grid, start_coords: tuple, end_coords: tuple):
    """
    Finds path on a provided grid between two nodes

    :param grid:
    :param start_coords:
    :param end_coords:
    :return: path_res, path_len_res
    """
    start_x, start_y = start_coords
    end_x, end_y = end_coords
    start = grid.node(start_x, start_y)
    end = grid.node(end_x, end_y)
    finder = AStarFinder(diagonal_movement=DiagonalMovement.never)
    path_res, runs = finder.find_path(start, end, grid)
    path_len_res = len(path_res)
    # print('operations:', runs, 'path length:', path_len)
    # print(grid.grid_str(path=path, start=start, end=end))
    grid.cleanup()
    return path_res, path_len_res

In [ ]:
def draw_path_to_map(path_to_draw: list, map_to_print: pd.DataFrame):
    path_marker = "🟥"
    print_map = map_to_print.copy()
    # FixMe: if first or last node is above or below the start or finish pop it of because it will otherwise overlap the stop or start
    #path_to_draw.pop(0)
    #path_to_draw.pop(len(path_to_draw)-1)
    for loc in path_to_draw:
        x, y = loc
        print_map.iat[y, x] = path_marker
    return print_map

In [ ]:
map_pathfinding_grid, map_pathfinding_matrix = instantiate_grid(map_pathfinding, export_matrix=True)

In [ ]:
def draw_from_lot_to_lot(start_lot: str|tuple, end_lot: str|tuple):
    if type(start_lot) is str:
        start_lot = master_houses_dict[start_lot][key_h_xy]
    if type(end_lot) is str:
        end_lot = master_houses_dict[end_lot][key_h_xy]

    path, path_len = find_path(map_pathfinding_grid, start_lot, end_lot)
    display_styled_map(draw_path_to_map(path, map_parcel))


In [ ]:
draw_from_lot_to_lot("JIX","IEG")

## Execute pathfinding

In [ ]:
debug_coord_s = (5,11)
debug_coord_e = (29,1)
map_pathfinding_grid, map_pathfinding_matrix = instantiate_grid(map_pathfinding, export_matrix=True)

path, path_len = find_path(map_pathfinding_grid, debug_coord_s, debug_coord_e)
display_styled_map(draw_path_to_map(path, map_parcel))


---
# Create district routes

## Split parcel locations into delivery districts

In [ ]:
def determine_delivery_district(coords):
    """
    Evaluates provided coordinates to return the delivery district it belongs to
    :param coords:
    :return:
    """
    x, y = coords
    for district, coords_range in delivery_districts.items():
        x_min, y_min = coords_range[0]
        x_max, y_max = coords_range[1]
        if x_min <= x <= x_max and y_min <= y <= y_max:
            return district
    raise ValueError

In [ ]:
def evaluate_lots_for_delivery_district():
    """
    Checks which lot with a parcel quantity of > 0 belongs into which delivery district
    """
    for lot, info in master_houses_dict.items():
        if info[key_h_parcels]>0:
            info[key_h_delivery_district] = determine_delivery_district(info[key_h_xy])

In [ ]:
evaluate_lots_for_delivery_district()

In [ ]:
pprint(master_houses_dict)

In [ ]:
def split_parcel_locations_into_districts() -> dict:
    """
    Splits all nodes that have parcels into a dict with the delivery district as key.
    The depot(s) are added to each district
    :return: {"A":{"AAB":(1,3),"AAD":(4,5)}, "B":{"DAF":(8,4),....}}
    """
    district_quantities = {}
    for district in delivery_districts.keys():
        district_nodes = {}
        for index, depot_coordinates in enumerate(depots_xy):
            depot_name = f"{name_string_depot}{index+1}"
            district_nodes[depot_name] = depot_coordinates
        for lot, info in master_houses_dict.items():
            if info[key_h_delivery_district] == district:
                district_nodes[lot] = info[key_h_xy]
        district_quantities[district] = district_nodes
    return district_quantities

In [ ]:
nodes_per_district = split_parcel_locations_into_districts()

In [ ]:
# DEBUG
for node in nodes_per_district["A"]:
    if name_string_depot not in node:
        print(master_houses_dict[node])

In [ ]:
pprint(nodes_per_district)

## Generate distance matrices within districts

In [ ]:
def instantiate_distance_matrices(nodes_in_district: dict, importing_matrices: bool = False) -> dict:
    """
    Creates individual (blank) distance matrices for all delivery districts.
    :param nodes_in_district:
    :param importing_matrices: Flag whether the blank distance matrices will be generated.
    :return: distance_matrices_dict
    {"A": <DF with all lots with parcels in district A>,
    "B": <DF with all lots with parcels in district A>}
    """
    distance_matrices_dict = {}
    if not importing_matrices:
        for district, nodes in nodes_in_district.items():
            lot_names = list(nodes.keys())
            distance_matrix = pd.DataFrame(index=lot_names, columns=lot_names)
            distance_matrices_dict[district] = distance_matrix
    return distance_matrices_dict

In [ ]:
instantiate_distance_matrices(nodes_per_district)

In [ ]:
def get_remaining_stops(stops: dict, cur_key:str) -> dict:
    """
    Evaluates the remaining nodes which the distance has not been calculated for yet for the current key.
    :param stops:
    :param cur_key:
    :return:
    """
    remaining_stops = {}
    found_key = False
    for key, value in stops.items():
        if key == cur_key:
            found_key = True
        elif found_key:
            remaining_stops[key] = value
    return remaining_stops

In [ ]:
def populate_distance_matrix(nodes_in_district: dict, dst_matrix: pd.DataFrame, district: str) -> pd.DataFrame:
    """
    Calculates the distances between each node
    :param dict nodes_in_district: Dict of all lots that will get parcels {'LHU': (38, 76), 'LHZ': (43, 76), 'LIF': (49, 76)}
    :param pd.DataFrame dst_matrix: DF of the instantiated distance matrix
    :param district
    :return:
    """
    return_df = dst_matrix
    for lot_a, node_a in nodes_in_district.items():
        print("------")
        remaining_stops = get_remaining_stops(stops=nodes_in_district, cur_key=lot_a).items()
        remaining_nodes = len(dict(remaining_stops).keys())
        print(f"Remaining nodes: {remaining_nodes}")
        print(f"Checking distances for: {lot_a}{node_a}")
        for lot_b, node_b in remaining_stops:
            _, distance = find_path(grid=map_pathfinding_grid,start_coords=node_a,end_coords=node_b)
            #print(f"[{district}] Distance from {lot_a}{node_a} to {lot_b}{node_b} = {distance} units")
            return_df.loc[lot_a, lot_b] = distance
            return_df.loc[lot_b, lot_a] = distance

    return_df = return_df.fillna(0)  # Fill distance between itself with 0
    return return_df

In [ ]:
print(nodes_per_district)

In [ ]:
# Populate distance matrices
if rerun_simulation:
    start_time = time.time()
    distance_matrices = instantiate_distance_matrices(nodes_in_district=nodes_per_district, importing_matrices=False)
    for district in delivery_districts.keys():
        print(f"Current district: {district}")
        tmp_df = populate_distance_matrix(nodes_per_district[district], distance_matrices[district], district)
        distance_matrices[district] = tmp_df
        print(tmp_df)
        save_file_name = f"{csv_distance_matrix_base}{district}"
        save_df_as_csv(df_to_save=tmp_df, csv_name_no_filetype=save_file_name, with_header_and_rows=True)
        print(f"Saved '{save_file_name}'.")
    pprint(distance_matrices)
    elapsed_time(start_time)
else:

    distance_matrices = instantiate_distance_matrices(nodes_in_district=nodes_per_district, importing_matrices=False)
    pprint(distance_matrices)
    column_names_dict = {}
    for district, distance_matrix in distance_matrices.items():
        column_names_dict[district] = distance_matrix.columns.tolist()

    #print("column_names_dict",column_names_dict)

    for district in delivery_districts.keys():
        #print(f"Column Names for district {district}: {column_names_dict[district]}")
        renamed_columns = {}
        for index, lot_name in enumerate(column_names_dict[district]):
            renamed_columns[index] = lot_name
        print(renamed_columns)
        print(f"Retrieving data from csv for district {district}")
        tmp_df = read_df_from_csv(f"{csv_distance_matrix_base}{district}", with_header_and_rows=True)
        #tmp_df = tmp_df.rename(columns=renamed_columns)
        distance_matrices[district] = tmp_df
        del tmp_df
    pprint(distance_matrices["A"])

In [ ]:
display(distance_matrices)

In [ ]:
test_df = read_df_from_csv("distance_matrix_district_J", True)
display(test_df)

## Create delivery routes

### Setup data model

In [ ]:
vrp_data = {}
vrp_data_key_distance_matrix = "distance_matrix"
vrp_data_key_num_vehicles = "num_vehicles"
vrp_data_key_depot = "depot"

In [ ]:
def prepare_data_model(distance_matrix: dict, number_of_vehicles: int = 1, depot_index: int = 0) -> dict:
    """
    Returns dictionary with distance matrix as np array, number of vehicles for the route calculating, and the index of the depot in the np array
    """
    vrp_data = {vrp_data_key_distance_matrix: distance_matrix.to_numpy(),
                vrp_data_key_num_vehicles: number_of_vehicles,
                vrp_data_key_depot: depot_index}
    return vrp_data


### Prepare data output

In [ ]:
def output_solution(data, manager, routing, solution):
    """
    Prints solution to console.
    :param data:
    :param manager:
    :param routing:
    :param solution:
    :return:
    """
    #print(f"Objective: {solution.ObjectiveValue()}")
    route_paths = {}
    route_distances = {}
    optimal_route_per_vehicle = {}
    for vehicle_id in range(data["num_vehicles"]):
        index = routing.Start(vehicle_id)
        print_routes = ""
        route_distance = 0
        optimal_route = []
        while not routing.IsEnd(index):
            route_index = manager.IndexToNode(index)
            print_routes += f" {route_index} -> "
            optimal_route.append(route_index)
            previous_index = index
            index = solution.Value(routing.NextVar(index))
            route_distance += routing.GetArcCostForVehicle(
                previous_index, index, vehicle_id)
        print_routes += f"{manager.IndexToNode(index)}"
        optimal_route.append(manager.IndexToNode(index))  # Add index of depot as last node
        route_distances[vehicle_id] = route_distance
        route_paths[vehicle_id] = print_routes
        optimal_route_per_vehicle[vehicle_id] = optimal_route
    return route_paths, optimal_route_per_vehicle, route_distances

In [ ]:
def extract_lot_names_from_route_indices(route_indices_per_vehicle: dict, distance_matrix: pd.DataFrame):
    lot_names = distance_matrix.columns.tolist()
    all_routes_with_lot_names_per_vehicle = {}
    for vehicle_id, route in route_indices_per_vehicle.items():
        route_with_lot_names = []
        for node_index in route:
            route_with_lot_names.append(lot_names[node_index])
        all_routes_with_lot_names_per_vehicle[vehicle_id]=route_with_lot_names
    return all_routes_with_lot_names_per_vehicle

### Instantiate model

In [ ]:
def evaluate_vrp(distance_matrix: dict, number_of_vehicles: int = 1) -> tuple[dict, dict, dict]:
    """
    Evaluates the vrp for one delivery district for each set delivery vehicle.
    :param distance_matrix:
    :param number_of_vehicles:
    :return: print_routes, route_indices, path_distances
    """
    # Prepare data model
    data = prepare_data_model(distance_matrix=distance_matrix,
                              number_of_vehicles=number_of_vehicles,
                              depot_index=0)
    # Setup index manager
    manager = pywrapcp.RoutingIndexManager(len(data['distance_matrix']),
                                           data['num_vehicles'],
                                           data['depot'])
    # Instantiate routing model
    routing = pywrapcp.RoutingModel(manager)

    def distance_callback(from_index, to_index):
        """Returns the distance between the two nodes."""
        # Convert from routing variable Index to distance matrix NodeIndex.
        from_node = manager.IndexToNode(from_index)
        to_node = manager.IndexToNode(to_index)
        return data['distance_matrix'][from_node][to_node]

    transit_callback_index = routing.RegisterTransitCallback(distance_callback)

    # Calculate cost of each path
    routing.SetArcCostEvaluatorOfAllVehicles(transit_callback_index)

    # Add distance constraint
    dimension_name = 'Distance'
    routing.AddDimension(
        transit_callback_index,
        0,  # no slack
        5000,  # vehicle maximum travel distance
        True,  # start cumulate to zero
        dimension_name)
    distance_dimension = routing.GetDimensionOrDie(dimension_name)
    distance_dimension.SetGlobalSpanCostCoefficient(100)

    # Setting first solution heuristic
    search_parameters = pywrapcp.DefaultRoutingSearchParameters()
    search_parameters.first_solution_strategy = (
        routing_enums_pb2.FirstSolutionStrategy.PATH_CHEAPEST_ARC)

    # Solve the problem
    solution = routing.SolveWithParameters(search_parameters)

    print_route_per_vehicle = {}
    route_indices_per_vehicle = {}
    path_distance_per_vehicle={}
    # Print solution on console.
    if solution:
        print_route_per_vehicle, route_indices_per_vehicle, path_distance_per_vehicle = output_solution(data, manager, routing, solution)
    else:
        print('No solution found !')

    return print_route_per_vehicle, route_indices_per_vehicle, path_distance_per_vehicle


### Execute model for each district

In [ ]:
def find_routes_for_delivery_districts(delivery_districts: dict, distance_matrices: dict):
    if rerun_simulation:
        print("Analysing delivery routes")
        routes_per_district = {}
        for district in delivery_districts:
            print(f"Analyzing delivery district: {district}")
            relevant_distance_matrix = distance_matrices[district]
            print_route_per_vehicle, route_indices_per_vehicle, path_distance_per_vehicle = evaluate_vrp(relevant_distance_matrix)
            routes_per_vehicle = extract_lot_names_from_route_indices(route_indices_per_vehicle, relevant_distance_matrix)
            for vehicle_id in routes_per_vehicle:
                print(f"Optimized route for vehicle {vehicle_id} in district {district}:")
                print(" -> ".join(routes_per_vehicle[vehicle_id]))
                print(f"Total distance for vehicle {vehicle_id} in district {district}: {path_distance_per_vehicle[vehicle_id]} units")
                print(f"----------")
            routes_per_district[district] = {}
            routes_per_district[district]["paths"] = routes_per_vehicle
            routes_per_district[district]["path_lengths"] = path_distance_per_vehicle
        print("Saving delivery routes to csv")
        df_routes_per_district = pd.DataFrame(routes_per_district)
        save_df_as_csv(df_routes_per_district, "vehicle_delivery_routes", True)

    else:
        print("Reading delivery routes from csv files")
        df_routes_per_district = read_df_from_csv("vehicle_delivery_routes", True)
    return df_routes_per_district


In [ ]:
routes_per_district = find_routes_for_delivery_districts(delivery_districts=delivery_districts, distance_matrices=distance_matrices)

### Populate master_routes_dict
<a id='sheesh'></a>

In [ ]:
def populate_master_dict_routes(df):
    """Populates the master_dict_route"""
    result = {}
    for index, row in df.iterrows():
        paths = row['paths']
        path_lengths = row['path_lengths']
        if isinstance(paths, str):
            paths = ast.literal_eval(paths)
        if isinstance(path_lengths, str):
            path_lengths = ast.literal_eval(path_lengths)
        result[index] = {
            'paths': paths,
            'path_lengths': path_lengths
        }
    return result

print(type(routes_per_district))

temp_ = routes_per_district.copy()
temp_ = temp_.T # Transpose df
pprint(temp_)
master_routes_dict = populate_master_dict_routes(temp_)
del temp_
print(master_routes_dict)

#print(master_dict_routes)

print(master_routes_dict["A"]["paths"][0])


## Visualize delivery route

In [ ]:
export_map_to_excel_with_formatting(map_parcel, excel_pathvis_wb, excel_pathvis_ws)

In [ ]:
# TODO visualizes

# Create milkruns for autonomous delivery

## Define sum function

Every point has to be visited once.
The robot has to go from the depot to the point and return (for each parcel)
Distance per house = <distance_from_depot_to_node> * 2

In [ ]:
def calculate_runs_per_house(lot_name, carry_capacity: int = 1):
    parcel_qty = master_houses_dict[lot_name][key_h_parcels]
    runs = math.ceil(parcel_qty / carry_capacity)
    master_houses_dict[key_h_delivery_runs_required] = runs
    return runs


In [28]:
def calculate_milk_run_distances(df: pd.DataFrame, district_name, carry_capacity:int = 1):
    """
    Calculate the sum of all values in row 0 of a DataFrame.
    :param df:
    :return:
    """
    headers = list(df)
    # Filter Depots from list
    filtered_headers = [col for col in headers if name_string_depot not in col]
    row = df.iloc[0]
    row_values = row.tolist()
    print("row_values", row_values)
    #print(filtered_headers)
    # Get quantities for each lot

    path_length = 0
    for index, lot_name in enumerate(filtered_headers):
        path_length_per_lot = 0
        run_multiplier = calculate_runs_per_house(lot_name, carry_capacity)
        distance = row_values[index]
        distance_both_ways = distance * 2
        distance_all_runs = distance_both_ways * run_multiplier
        path_length_per_lot += distance_all_runs
        print(f"Path length for {lot_name}= {path_length} Parcels={master_houses_dict[lot_name][key_h_parcels]}, Distance from Depot={row_values[index]}")
        path_length += path_length_per_lot
    #print(row.tolist())
    return path_length


In [29]:
pprint(master_houses_dict["AEF"])

{'delivery_district': '',
 'delivery_runs_required': 0,
 'households': 0,
 'lot_use': None,
 'parcels': 0,
 'path_finding_val': 0,
 'xy': (9, 1)}


In [30]:
print(distance_matrices["A"])
print(calculate_milk_run_distances(distance_matrices["A"], "A"))

NameError: name 'distance_matrices' is not defined

In [ ]:
def populate_autonomous_delivery_dict():
    for district, distance_matrix in distance_matrices.items():
        master_autonomous_dict[district] = {}
        print(f"Calculating milk run distances for district {district}")
        distance = calculate_milk_run_distances(df=distance_matrix, carry_capacity=par_sys_aut_vehicle_capacity)
        master_autonomous_dict[district][key_a_distance] = distance


# Model output

In [ ]:
def get_model_output():
    out_parcels = 0
    out_stops = 0
    out_delivered = 0
    out_distance_conventional = 0
    out_distance_autonomous = 0
    for lot, info in master_houses_dict.items():
        if info[key_h_parcels] > 0:
            out_parcels += int(info[key_h_parcels])
            out_stops += 1
    for district, info in master_routes_dict.items():
        out_distance_conventional += info[key_r_path_lengths]
    for district, info in master_autonomous_dict.items():
        out_distance_autonomous += info[key_a_distance]

    out_drop_factor = out_parcels / out_stops